In [37]:
import pandas as pd
import scipy.io as sio
import numpy as np
import datetime
import plotly.express as px
from plotly.subplots import make_subplots
import plotly.graph_objects as go
import re

def Array_To_DataFrame(matDF, varName) :
    npArray = np.array([])
    for i in range (matDF[varName].shape[0]) :
        npArray = np.concatenate((npArray, matDF[varName][i].flatten()))
    return npArray

def matFile_To_DF(matFile) :
    tempDF = sio.loadmat(matFile)
    matDataMidFiltered = {dictKey:dictValue for dictKey, dictValue in tempDF.items() if dictKey[0] != '_'}
    matMidDF = pd.DataFrame({dictKey: np.array(dictValue).flatten() for dictKey, dictValue in matDataMidFiltered.items()})
    return matMidDF
    
#import downriver bottom data
matDataMini1 = sio.loadmat('2013_14\\hobo_ml_3828_Dep3.mat')
matDataMini2 = sio.loadmat('2013_14\\hobo_mlriver_4773_Dep1.mat')
matDataMini3 = sio.loadmat('2013_14\\hobo_mlriver_4774_Dep2.mat')
#matDataMini4 = sio.loadmat('2013_14\\hobo_mlriver_5055_p_Dep1.mat')
#matDataMini5 = sio.loadmat('2013_14\\hobo_mlriver_5055_p_Dep2.mat')
#matDataMini6 = sio.loadmat('2013_14\\hobo_mlriver_5055_p_Dep3.mat')

#mat lab date origin
origin = np.datetime64('0000-01-01', 'D') - np.timedelta64(1, 'D')

matDataMini1Filtered = {dictKey:dictValue for dictKey, dictValue in matDataMini1.items() if dictKey[0] != '_'}
matMini1DF = pd.DataFrame({dictKey: np.array(dictValue).flatten() for dictKey, dictValue in matDataMini1Filtered.items()})
matDataMini2Filtered = {dictKey:dictValue for dictKey, dictValue in matDataMini2.items() if dictKey[0] != '_'}
matMini2DF = pd.DataFrame({dictKey: np.array(dictValue).flatten() for dictKey, dictValue in matDataMini2Filtered.items()})
matDataMini3Filtered = {dictKey:dictValue for dictKey, dictValue in matDataMini3.items() if dictKey[0] != '_'}
matMini3DF = pd.DataFrame({dictKey: np.array(dictValue).flatten() for dictKey, dictValue in matDataMini3Filtered.items()})
'''
matDataMini4Filtered = {dictKey:dictValue for dictKey, dictValue in matDataMini4.items() if dictKey[0] != '_'}
matMini4DF = pd.DataFrame({dictKey: np.array(dictValue).flatten() for dictKey, dictValue in matDataMini4Filtered.items()})
matDataMini5Filtered = {dictKey:dictValue for dictKey, dictValue in matDataMini5.items() if dictKey[0] != '_'}
matMini5DF = pd.DataFrame({dictKey: np.array(dictValue).flatten() for dictKey, dictValue in matDataMini5Filtered.items()})
matDataMini6Filtered = {dictKey:dictValue for dictKey, dictValue in matDataMini6.items() if dictKey[0] != '_'}
matMini6DF = pd.DataFrame({dictKey: np.array(dictValue).flatten() for dictKey, dictValue in matDataMini6Filtered.items()})
'''

#matMiniDF = pd.concat([matMini1DF, matMini2DF,matMini3DF, matMini4DF,matMini5DF, matMini6DF])
matMiniDF = pd.concat([matMini1DF, matMini2DF,matMini3DF])

matMiniDF = matMiniDF.sort_values(['DN'], ascending = [True]).reset_index(drop = True)

masterTimeDF = np.linspace(matMiniDF['DN'][0], matMiniDF['DN'][len(matMiniDF['DN']) - 1], 38329)
minilanderSalinity = np.interp(masterTimeDF, matMiniDF['DN'], matMiniDF['S'], left = np.nan, right = np.nan)
minilanderTemperature = np.interp(masterTimeDF, matMiniDF['DN'], matMiniDF['T'], left = np.nan, right = np.nan)

tmsMiniriver = (masterTimeDF * np.timedelta64(24*3600000, 'ms') + origin + np.timedelta64(500, 'ms')).astype('datetime64[s]')
matMiniDF = pd.DataFrame({'DN' : tmsMiniriver, 'S' : minilanderSalinity, 'T' : minilanderTemperature})

downRiverDF = pd.read_csv('downriver_2013_2014_processed.csv', parse_dates = ['DN'])
downRiverDF = downRiverDF.sort_values(['DN'], ascending = [True])

#reading in flow data
flowDF = pd.read_csv('2013_2014alsea.csv')
flowDF['fRate'] = flowDF['max_va'] * 0.0283168
#create a new column for flow dates
for index, row in flowDF.iterrows():
    calcDate = pd.Timestamp(year=int(row['begin_yr']), month=int(row['month_nu']), day=int(row['day_nu']))
    flowDF.loc[index, 'DN'] = calcDate

tmsFlow = flowDF['DN']

# Second interval : Dec 13 to Jan 14
avgMiniSal = np.array(matMiniDF['S'].to_numpy(), copy = True)
avgDownBottomSal = np.array(downRiverDF['BottomSalCorrected'].to_numpy(), copy = True)
for idx in range(len(tmsMiniriver)):
    if not ((tmsMiniriver[idx] > pd.Timestamp('2013-12-13') and tmsMiniriver[idx] < pd.Timestamp('2014-01-14'))):
        avgMiniSal[idx] = np.nan
for idx in range(len(downRiverDF['DN'])):
    if not ((downRiverDF['DN'][idx] > pd.Timestamp('2013-12-13') and downRiverDF['DN'][idx] < pd.Timestamp('2013-12-19'))):
        avgDownBottomSal[idx] = np.nan
scaleFactor1 = np.nanmax(avgDownBottomSal)/np.nanmax(avgMiniSal)

# Third interval - Jan 16 to March 12
avgMiniSal = np.array(matMiniDF['S'].to_numpy(), copy = True)
avgDownBottomSal = np.array(downRiverDF['BottomSalCorrected'].to_numpy(), copy = True)
for idx in range(len(tmsMiniriver)):
    if not ((tmsMiniriver[idx] > pd.Timestamp('2013-12-13') and tmsMiniriver[idx] < pd.Timestamp('2014-01-14'))):
        avgMiniSal[idx] = np.nan
for idx in range(len(downRiverDF['DN'])):
    if not ((downRiverDF['DN'][idx] > pd.Timestamp('2014-01-16') and downRiverDF['DN'][idx] < pd.Timestamp('2014-01-28'))):
        avgDownBottomSal[idx] = np.nan
scaleFactor3 = np.nanmax(avgDownBottomSal)/np.nanmax(avgMiniSal)

for idx in range(len(tmsMiniriver)):
    if (tmsMiniriver[idx] > pd.Timestamp('2013-12-13') and tmsMiniriver[idx] < pd.Timestamp('2014-01-14')):
        matMiniDF.loc[idx, 'S'] = matMiniDF['S'][idx] * scaleFactor1
    elif (tmsMiniriver[idx] > pd.Timestamp('2014-01-16') and tmsMiniriver[idx] < pd.Timestamp('2014-03-12')):
        matMiniDF.loc[idx, 'S'] = matMiniDF['S'][idx] * scaleFactor3
    elif (tmsMiniriver[idx] > pd.Timestamp('2013-10-30') and tmsMiniriver[idx] < pd.Timestamp('2013-12-11')):
        pass
    else:
        matMiniDF.loc[idx, 'S'] = np.nan



timedMiniDF = pd.DataFrame({'DN' : tmsMiniriver, 'Salinity' : matMiniDF['S'], 'Temperature' : matMiniDF['T']})
timedMiniDF.to_csv('minilander_2013_2014_processed.csv', index=False)


tempFigLabels = ['Miniriver']
tempfig = px.line(x = tmsMiniriver, y = [matMiniDF['T']], color_discrete_sequence= ["purple"], title = "Mini")
for idx in range(len(tempFigLabels)):
    tempfig.data[idx].name = tempFigLabels[idx]
    tempfig.data[idx].hovertemplate = 'variable=' + tempFigLabels[idx] + '<br>x=%{x}<br>value=%{y}<extra></extra>'
    tempfig.data[idx].legendgroup = tempFigLabels[idx]
salfig = px.line(x= tmsMiniriver, y = [matMiniDF['S']], color_discrete_sequence = ["purple"], title = "Mini")
for idx in range(len(tempFigLabels)):
    salfig.data[idx].name = tempFigLabels[idx]
    salfig.data[idx].hovertemplate = 'variable=' + tempFigLabels[idx] + '<br>x=%{x}<br>value=%{y}<extra></extra>'
    salfig.data[idx].legendgroup = tempFigLabels[idx]

flowFigLabel = ['Flow Rate']
flowfig = px.line(x = tmsFlow, y = [flowDF['fRate']], color_discrete_sequence= ["green"], title = "Flow Rate")
for idx in range(len(flowFigLabel)):
    flowfig.data[idx].name = flowFigLabel[idx]
    flowfig.data[idx].hovertemplate = 'variable=' + flowFigLabel[idx] + '<br>x=%{x}<br>value=%{y}<extra></extra>'
    flowfig.data[idx].legendgroup = flowFigLabel[idx]

tempfig.update_layout(title=dict(text= "Bottom Temperature for 2013-2014", font=dict(size=25)))
tempfig.update_xaxes(tickangle=30)
tempfig.update_xaxes(rangeslider_visible=True)
tempfig.update_xaxes(range = [pd.Timestamp(preTimeStamp * np.timedelta64(1, 'D') + origin),pd.Timestamp('2014-03-17')])

salfig.update_layout(title=dict(text= "Bottom Salinity for 2013-2014", font=dict(size=25)))
salfig.update_xaxes(tickangle=30)
salfig.update_xaxes(rangeslider_visible=True)
salfig.update_xaxes(range = [pd.Timestamp(preTimeStamp * np.timedelta64(1, 'D') + origin),pd.Timestamp('2014-03-17')])

flowfig.update_layout(title=dict(text= "Flow Rate for 2013-2014", font=dict(size=25)))
flowfig.update_xaxes(tickangle=30)
flowfig.update_xaxes(rangeslider_visible=True)
flowfig.update_xaxes(range = [pd.Timestamp(preTimeStamp * np.timedelta64(1, 'D') + origin),pd.Timestamp('2014-03-17')])

tempfig.update_layout(xaxis_title="Date", yaxis_title="Temperature (°C)", legend_title="Locations")
salfig.update_layout(xaxis_title="Date", yaxis_title="Salinity", legend_title="Locations")
flowfig.update_layout(xaxis_title="Date", yaxis_title="Cubic Meters per Second",legend_title="Locations")

tempfig.show()
salfig.show()
flowfig.show()



